In [30]:
from pathlib import Path
import time

from utils.config import cfg_from_yaml_file
from tools import builder

import torch
import numpy as np
import open3d as o3d
import plotly.graph_objects as go

In [13]:
def show_points(points):
    fig = go.Figure(
        data=[
            go.Scatter3d(
                x=points[:, 0],
                y=points[:, 1],
                z=points[:, 2],
                mode="markers",
                marker=dict(size=3, color=points[:, 2], colorscale="hot"),
            ),
        ]
    )
    fig.update_layout(
        autosize=False,
        width=800,
        height=800,
        scene=dict(aspectmode='data')
    )
    fig.show()


def save_pcd(point_array: np.ndarray, path: Path):
    pcd = o3d.geometry.PointCloud()
    pcd.points = o3d.utility.Vector3dVector(point_array)

    path_str = path.with_suffix(".pcd").as_posix()
    o3d.io.write_point_cloud(path_str, pcd)

In [26]:
norm_dict = {'scale': 1.2462792, 'center': [-0.61431795, -0.21019769,  0.08693554]}

In [42]:
partial_path = Path('/home/dmitry/PoinTr/data/PCN_full/test/partial/00000000/000333_0_Lower_A3135444636324533413743474234/73.pcd')
complete_path = Path('/home/dmitry/PoinTr/data/PCN_full/test/complete/00000000/000333_0_Lower_A3135444636324533413743474234/73.pcd')
ckpt_path = Path('/home/dmitry/PoinTr/experiments/AdaPoinTr/PCN_models/landmarks_full_emd/ckpt-last.pth')
cfg_path = Path('/home/dmitry/PoinTr/cfgs/PCN_models/AdaPoinTr.yaml')
save_path = Path('/home/dmitry/PoinTr/data/Nora')
save_path.mkdir(exist_ok=True)

config = cfg_from_yaml_file(cfg_path)
base_model = builder.model_builder(config.model)
builder.load_model(base_model, ckpt_path)

2023-05-09 13:31:22,430 - MODEL - INFO - Transformer with config {'NAME': 'AdaPoinTr', 'num_query': 384, 'num_points': 256, 'center_num': [512, 256], 'global_feature_dim': 1024, 'encoder_type': 'graph', 'decoder_type': 'fc', 'encoder_config': {'embed_dim': 384, 'depth': 6, 'num_heads': 6, 'k': 8, 'n_group': 2, 'mlp_ratio': 2.0, 'block_style_list': ['attn-graph', 'attn', 'attn', 'attn', 'attn', 'attn'], 'combine_style': 'concat'}, 'decoder_config': {'embed_dim': 384, 'depth': 8, 'num_heads': 6, 'k': 8, 'n_group': 2, 'mlp_ratio': 2.0, 'self_attn_block_style_list': ['attn-graph', 'attn', 'attn', 'attn', 'attn', 'attn', 'attn', 'attn'], 'self_attn_combine_style': 'concat', 'cross_attn_block_style_list': ['attn-graph', 'attn', 'attn', 'attn', 'attn', 'attn', 'attn', 'attn'], 'cross_attn_combine_style': 'concat'}}


/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
/home/dmitry/PoinTr
using group version 2
Loading weights from /home/dmitry/PoinTr/experiments/AdaPoinTr/PCN_models/landmarks_full_emd/ckpt-last.pth...
ckpts @ 529 epoch( performance = {'F-Score': 0.050480859123612984, 'CDL1': 37.73981007491008, 'CDL2': 17.776811936114093, 'EMDistance': 0.0})


In [43]:
base_model.cuda().eval()

pcd_np = np.asarray(o3d.io.read_point_cloud(partial_path.as_posix()).points)
pcd = torch.from_numpy(pcd_np).float().cuda()

gt_np = np.asarray(o3d.io.read_point_cloud(complete_path.as_posix()).points)
gt = torch.from_numpy(gt_np)

start = time.time()
prediction = base_model(pcd.unsqueeze(0))
end = time.time()
pr_np = prediction[0].detach().cpu().numpy()


In [44]:
end - start

0.06415438652038574

In [29]:
show_points(np.concatenate((pcd_np, pr_np)))

In [28]:
show_points(np.concatenate((pcd_np, gt_np)))